# 신경망 하이퍼파라미터 튜닝하기
조정할 하이퍼파라미터가 매우 많음. 구조뿐만 아니라 층의 개수, 층마다 있는 뉴런 갯수, 각 층에서 사용하는 활성화함수, 가중치 초기화 전략 등 많은 것을 바꿀 수 있음. 그렇다면 어떤 조합이 가장 최적인지 어떻게 확인할까?  
한 가지 방법은 이전 사이킷런에서 했던 것처럼 여러 조합을 시도해보고 검증셋에서 가장 좋은 성능을 내는 것을 고르는 것임.  
즉 **그리드서치나 랜덤서치**를 이용하는 것. 이용하려면 **케라스 모델을 사이킷런 추정기처럼 바꾸어야 함.**

In [6]:
import tensorflow as tf
from tensorflow import keras

In [21]:
def build_model(n_hidden=1, n_neu=30, learning_rate=3e-3, input_shape=[8]):
    model = keras.models.Sequential()
    model.add(keras.layers.InputLayer(input_shape=input_shape))
    for layer in range(n_hidden):
        model.add(keras.layers.Dense(n_neu, activation="relu"))
    model.add(keras.layers.Dense(1))
    optimizer = keras.optimizers.SGD(lr=learning_rate)
    model.compile(loss="mse", optimizer=optimizer)
    return model

In [22]:
from sklearn.datasets import fetch_california_housing
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler

housing = fetch_california_housing()

x_train_full, x_test, y_train_full, y_test = train_test_split(
    housing.data, housing.target)
x_train, x_val, y_train, y_val = train_test_split(
    x_train_full, y_train_full)

scaler = StandardScaler()
x_train = scaler.fit_transform(x_train)
x_val = scaler.transform(x_val)
x_test = scaler.transform(x_test)

x_train_a, x_train_b = x_train[:, :5], x_train[:, 2:]
x_val_a, x_val_b = x_val[:, :5], x_val[:, 2:]
x_test_a, x_test_b = x_test[:, :5], x_test[:, 2:]

In [23]:
keras_reg = keras.wrappers.scikit_learn.KerasRegressor(build_model)

**KerasRegressor** 객체는 build_model() 함수로 만들어진 케라스 모델을 감싸는 간단한 래퍼임.  
이제 일반적인 사이킷런 회귀 추정기처럼 이 객체를 사용할 수 있음.

In [24]:
keras_reg.fit(x_train, y_train, epochs=100,
             validation_data=(x_val, y_val),
             callbacks=[keras.callbacks.EarlyStopping(patience=10)])

Epoch 1/100
363/363 [==============================] - 1s 671us/step - loss: 1.6674 - val_loss: 0.6457
Epoch 2/100
363/363 [==============================] - 0s 475us/step - loss: 0.6971 - val_loss: 0.5625
Epoch 3/100
363/363 [==============================] - 0s 546us/step - loss: 0.6056 - val_loss: 0.5150
Epoch 4/100
363/363 [==============================] - 0s 533us/step - loss: 0.5361 - val_loss: 0.4830
Epoch 5/100
363/363 [==============================] - 0s 517us/step - loss: 0.5145 - val_loss: 0.4628
Epoch 6/100
363/363 [==============================] - 0s 497us/step - loss: 0.5075 - val_loss: 0.4581
Epoch 7/100
363/363 [==============================] - 0s 503us/step - loss: 0.5146 - val_loss: 0.4390
Epoch 8/100
363/363 [==============================] - 0s 514us/step - loss: 0.4488 - val_loss: 0.4301
Epoch 9/100
363/363 [==============================] - 0s 533us/step - loss: 0.4558 - val_loss: 0.4261
Epoch 10/100
363/363 [==============================] - 0s 550us/step - l

Epoch 80/100
363/363 [==============================] - 0s 478us/step - loss: 0.3727 - val_loss: 0.3277
Epoch 81/100
363/363 [==============================] - 0s 492us/step - loss: 0.3465 - val_loss: 0.3274
Epoch 82/100
363/363 [==============================] - 0s 484us/step - loss: 0.3360 - val_loss: 0.3280
Epoch 83/100
363/363 [==============================] - 0s 486us/step - loss: 0.3478 - val_loss: 0.3274
Epoch 84/100
363/363 [==============================] - 0s 478us/step - loss: 0.3532 - val_loss: 0.3264
Epoch 85/100
363/363 [==============================] - 0s 470us/step - loss: 0.3394 - val_loss: 0.3255
Epoch 86/100
363/363 [==============================] - 0s 484us/step - loss: 0.3366 - val_loss: 0.3258
Epoch 87/100
363/363 [==============================] - 0s 484us/step - loss: 0.3487 - val_loss: 0.3237
Epoch 88/100
363/363 [==============================] - 0s 486us/step - loss: 0.3494 - val_loss: 0.3238
Epoch 89/100
363/363 [==============================] - 0s 486us

In [25]:
mse_test = keras_reg.score(x_test, y_test)
y_pred = keras_reg.predict(x_test)
mse_test, y_pred[:3]

162/162 [==============================] - 0s 335us/step - loss: 0.3315


(-0.33153578639030457, array([3.892997 , 2.7122774, 1.2784774], dtype=float32))

fit() 메서드에 지정한 모든 매개변수는 케라스 모델로 전달됨.  
사이킷런은 손실이 아니라 점수를 계산하기 때문에 score메서드로 출력한 점수는 음수의 MSE임  

In [ ]:
import numpy as np
from scipy.stats import reciprocal
from sklearn.model_selection import RandomizedSearchCV

param_distribs = {
    "n_hidden" : [0, 1, 2, 3],
    "n_neu" : np.arange(1, 100).tolist(),
    "learning_rate" : reciprocal(3e-4, 3e-2).rvs(1000).tolist()
}

rnd_search = RandomizedSearchCV(keras_reg, param_distribs, n_iter=10, cv=3)

In [ ]:
keras_reg.get_params()

In [ ]:
rnd_search.fit(x_train, y_train, epochs=100,
              validation_data=(x_val, y_val),
              callbacks=[keras.callbacks.EarlyStopping(patience=10)])

RandomizedSearchCV는 k폴드 교차검증을 사용하기 때문에 x_val, y_val을 검증에 사용하지 않음. 대신 해당 이터레이션의 학습 조기 종료에 사용함.  
신기하게 epochs=100으로 설정하고 fit을 했더니 각 옵션에 따라 100번까지 반복함. 총 반복횟수는 n_iter에 설정한 10인가??  
마지막 부분 에러는 왜 나는지 모르겠음...  
> 에러가 나는 이유는 사이킷런 변화에 따른 케라스문제라고 함.  
사이킷런에서 사용할 수 있는 반복가능한 형태가 아니라서 그런듯?  
그래서 **tolist(), rvs(1000).tolist()** 처럼 반복가능하도록 변경하여 실행하면 된다고함

In [28]:
rnd_search.best_params_

{'learning_rate': 0.019571940651507583, 'n_hidden': 3, 'n_neu': 80}

In [29]:
rnd_search.best_score_

-0.2983220914999644

In [31]:
best_model = rnd_search.best_estimator_

AttributeError: 'RandomizedSearchCV' object has no attribute 'best_estimator_'

마지막에 에러가 나서 best_estimator 특성이 안만들어진듯 ㅡㅡ

In [49]:
from sklearn.model_selection import GridSearchCV

param_grids = {
    "n_hidden" : [0, 1, 2, 3],
    "n_neu" : np.arange(1, 100, 3),
    "learning_rate" : [0.003, 0.005, 0.001, 0.0005]
}

grid_search = GridSearchCV(keras_reg, param_grids, cv=3)

In [50]:
grid_search.fit(x_train, y_train, epochs=100,
              validation_data=(x_val, y_val),
              callbacks=[keras.callbacks.EarlyStopping(patience=10)])

Epoch 1/100
242/242 [==============================] - 0s 795us/step - loss: 5.4078 - val_loss: 1.0869
Epoch 2/100
242/242 [==============================] - 0s 563us/step - loss: 0.9341 - val_loss: 0.7295
Epoch 3/100
242/242 [==============================] - 0s 562us/step - loss: 0.7915 - val_loss: 0.6737
Epoch 4/100
242/242 [==============================] - 0s 651us/step - loss: 0.7317 - val_loss: 0.6434
Epoch 5/100
242/242 [==============================] - 0s 612us/step - loss: 0.7096 - val_loss: 0.6160
Epoch 6/100
242/242 [==============================] - 0s 514us/step - loss: 0.6636 - val_loss: 0.5963
Epoch 7/100
242/242 [==============================] - 0s 552us/step - loss: 0.6392 - val_loss: 0.5787
Epoch 8/100
242/242 [==============================] - 0s 481us/step - loss: 0.6342 - val_loss: 0.5644
Epoch 9/100
242/242 [==============================] - 0s 561us/step - loss: 0.5734 - val_loss: 0.5538
Epoch 10/100
242/242 [==============================] - 0s 543us/step - l

242/242 [==============================] - 0s 550us/step - loss: 0.5388 - val_loss: 0.5074
Epoch 18/100
242/242 [==============================] - 0s 557us/step - loss: 0.5807 - val_loss: 0.5072
Epoch 19/100
242/242 [==============================] - 0s 553us/step - loss: 0.5375 - val_loss: 0.5071
Epoch 20/100
242/242 [==============================] - 0s 553us/step - loss: 0.5397 - val_loss: 0.5060
Epoch 21/100
242/242 [==============================] - 0s 563us/step - loss: 0.5727 - val_loss: 0.5056
Epoch 22/100
242/242 [==============================] - 0s 535us/step - loss: 0.5274 - val_loss: 0.5050
Epoch 23/100
242/242 [==============================] - 0s 567us/step - loss: 0.5512 - val_loss: 0.5063
Epoch 24/100
242/242 [==============================] - 0s 531us/step - loss: 0.5698 - val_loss: 0.5066
Epoch 25/100
242/242 [==============================] - 0s 488us/step - loss: 0.5441 - val_loss: 0.5062
Epoch 26/100
242/242 [==============================] - 0s 495us/step - loss:

242/242 [==============================] - 0s 542us/step - loss: 0.5923 - val_loss: 0.5463
Epoch 7/100
242/242 [==============================] - 0s 596us/step - loss: 0.5785 - val_loss: 0.5380
Epoch 8/100
242/242 [==============================] - 0s 548us/step - loss: 0.5619 - val_loss: 0.5316
Epoch 9/100
242/242 [==============================] - 0s 507us/step - loss: 0.5530 - val_loss: 0.5269
Epoch 10/100
242/242 [==============================] - 0s 584us/step - loss: 0.5489 - val_loss: 0.5257
Epoch 11/100
242/242 [==============================] - 0s 577us/step - loss: 0.5637 - val_loss: 0.5185
Epoch 12/100
242/242 [==============================] - 0s 566us/step - loss: 0.5490 - val_loss: 0.5157
Epoch 13/100
242/242 [==============================] - 0s 552us/step - loss: 0.5551 - val_loss: 0.5135
Epoch 14/100
242/242 [==============================] - 0s 546us/step - loss: 0.5723 - val_loss: 0.5106
Epoch 15/100
242/242 [==============================] - 0s 483us/step - loss: 0.

242/242 [==============================] - 0s 556us/step - loss: 0.5552 - val_loss: 0.5075
Epoch 16/100
242/242 [==============================] - 0s 553us/step - loss: 0.5313 - val_loss: 0.5081
Epoch 17/100
242/242 [==============================] - 0s 569us/step - loss: 0.5240 - val_loss: 0.5085
Epoch 18/100
242/242 [==============================] - 0s 512us/step - loss: 0.5550 - val_loss: 0.5042
Epoch 19/100
242/242 [==============================] - 0s 572us/step - loss: 0.5431 - val_loss: 0.5068
Epoch 20/100
242/242 [==============================] - 0s 540us/step - loss: 0.5620 - val_loss: 0.5049
Epoch 21/100
242/242 [==============================] - 0s 564us/step - loss: 0.5699 - val_loss: 0.5052
Epoch 22/100
242/242 [==============================] - 0s 502us/step - loss: 0.5643 - val_loss: 0.5073
Epoch 23/100
242/242 [==============================] - 0s 594us/step - loss: 0.5445 - val_loss: 0.5082
Epoch 24/100
242/242 [==============================] - 0s 522us/step - loss:

242/242 [==============================] - 0s 554us/step - loss: 0.5283 - val_loss: 0.5019
Epoch 18/100
242/242 [==============================] - 0s 553us/step - loss: 0.5350 - val_loss: 0.5020
Epoch 19/100
242/242 [==============================] - 0s 555us/step - loss: 0.5572 - val_loss: 0.5012
Epoch 20/100
242/242 [==============================] - 0s 548us/step - loss: 0.5395 - val_loss: 0.5033
Epoch 21/100
242/242 [==============================] - 0s 546us/step - loss: 0.5417 - val_loss: 0.5021
Epoch 22/100
242/242 [==============================] - 0s 551us/step - loss: 0.4896 - val_loss: 0.5017
Epoch 23/100
242/242 [==============================] - 0s 553us/step - loss: 0.5244 - val_loss: 0.5014
Epoch 24/100
242/242 [==============================] - 0s 488us/step - loss: 0.5512 - val_loss: 0.5022
Epoch 25/100
242/242 [==============================] - 0s 488us/step - loss: 0.5243 - val_loss: 0.5005
Epoch 26/100
242/242 [==============================] - 0s 549us/step - loss:

...

242/242 [==============================] - 0s 542us/step - loss: 0.5132 - val_loss: 0.5048
Epoch 79/100
242/242 [==============================] - 0s 531us/step - loss: 0.5340 - val_loss: 0.5054
Epoch 80/100
242/242 [==============================] - 0s 544us/step - loss: 0.5488 - val_loss: 0.5042
Epoch 81/100
242/242 [==============================] - 0s 552us/step - loss: 0.5452 - val_loss: 0.5050
Epoch 82/100
242/242 [==============================] - 0s 531us/step - loss: 0.5342 - val_loss: 0.5046
Epoch 83/100
242/242 [==============================] - 0s 547us/step - loss: 0.5520 - val_loss: 0.5046
Epoch 84/100
242/242 [==============================] - 0s 548us/step - loss: 0.5638 - val_loss: 0.5049
Epoch 85/100
242/242 [==============================] - 0s 551us/step - loss: 0.5336 - val_loss: 0.5051
Epoch 86/100
242/242 [==============================] - 0s 535us/step - loss: 0.5239 - val_loss: 0.5051
Epoch 87/100
242/242 [==============================] - 0s 552us/step - loss:

242/242 [==============================] - 0s 581us/step - loss: 0.5438 - val_loss: 0.5023
Epoch 67/100
242/242 [==============================] - 0s 585us/step - loss: 0.5445 - val_loss: 0.5021
Epoch 68/100
242/242 [==============================] - 0s 577us/step - loss: 0.5234 - val_loss: 0.5021
Epoch 69/100
242/242 [==============================] - 0s 585us/step - loss: 0.5475 - val_loss: 0.5021
Epoch 70/100
242/242 [==============================] - 0s 581us/step - loss: 0.5368 - val_loss: 0.5019
Epoch 71/100
242/242 [==============================] - 0s 577us/step - loss: 0.5437 - val_loss: 0.5019
Epoch 72/100
242/242 [==============================] - 0s 581us/step - loss: 0.5351 - val_loss: 0.5017
Epoch 73/100
242/242 [==============================] - 0s 598us/step - loss: 0.5361 - val_loss: 0.5017
Epoch 74/100
242/242 [==============================] - 0s 589us/step - loss: 0.5266 - val_loss: 0.5016
Epoch 75/100
242/242 [==============================] - 0s 569us/step - loss:

242/242 [==============================] - 0s 585us/step - loss: 0.5366 - val_loss: 0.5120
Epoch 45/100
242/242 [==============================] - 0s 585us/step - loss: 0.5377 - val_loss: 0.5114
Epoch 46/100
242/242 [==============================] - 0s 581us/step - loss: 0.5662 - val_loss: 0.5112
Epoch 47/100
242/242 [==============================] - 0s 581us/step - loss: 0.5745 - val_loss: 0.5102
Epoch 48/100
242/242 [==============================] - 0s 581us/step - loss: 0.5374 - val_loss: 0.5100
Epoch 49/100
242/242 [==============================] - 0s 581us/step - loss: 0.5453 - val_loss: 0.5099
Epoch 50/100
242/242 [==============================] - 0s 598us/step - loss: 0.5363 - val_loss: 0.5092
Epoch 51/100
242/242 [==============================] - 0s 606us/step - loss: 0.5544 - val_loss: 0.5085
Epoch 52/100
242/242 [==============================] - 0s 593us/step - loss: 0.5658 - val_loss: 0.5084
Epoch 53/100
242/242 [==============================] - 0s 581us/step - loss:

242/242 [==============================] - 0s 577us/step - loss: 0.5628 - val_loss: 0.5273
Epoch 23/100
242/242 [==============================] - 0s 585us/step - loss: 0.5640 - val_loss: 0.5257
Epoch 24/100
242/242 [==============================] - 0s 585us/step - loss: 0.5398 - val_loss: 0.5246
Epoch 25/100
242/242 [==============================] - 0s 598us/step - loss: 0.5629 - val_loss: 0.5238
Epoch 26/100
242/242 [==============================] - 0s 647us/step - loss: 0.5527 - val_loss: 0.5225
Epoch 27/100
242/242 [==============================] - 0s 610us/step - loss: 0.5663 - val_loss: 0.5213
Epoch 28/100
242/242 [==============================] - 0s 585us/step - loss: 0.5582 - val_loss: 0.5206
Epoch 29/100
242/242 [==============================] - 0s 618us/step - loss: 0.5455 - val_loss: 0.5193
Epoch 30/100
242/242 [==============================] - 0s 606us/step - loss: 0.5563 - val_loss: 0.5186
Epoch 31/100
242/242 [==============================] - 0s 581us/step - loss:

KeyboardInterrupt: 

In [51]:
reciprocal(3e-4, 3e-2).rvs(1000).tolist()

[0.007878725196306731,
 0.0011490341781252883,
 0.0019668671364266145,
 0.002267434712128751,
 0.01589110615226183,
 0.00031019208225335,
 0.003976571749842812,
 0.00571979656026133,
 0.029488693590488443,
 0.0034893015189222283,
 0.006289180925796922,
 0.010146470616025938,
 0.0003190242024438458,
 0.0021596353138768555,
 0.0006272713884569886,
 0.011048878707902967,
 0.000925888608382956,
 0.0019788283172300957,
 0.010443458827457777,
 0.0037185883121800874,
 0.003915454222107144,
 0.015067729077778964,
 0.015452912278380707,
 0.01918507777554375,
 0.00630208554326792,
 0.013066572106491628,
 0.0015618904283710648,
 0.005623596098526795,
 0.005655558698446393,
 0.019923304806269165,
 0.005153666162509092,
 0.01850911194101693,
 0.004393512004384089,
 0.0005629221587020159,
 0.004708918709253045,
 0.0003903363522165425,
 0.004082366543705869,
 0.0009706225234911968,
 0.009436353697314177,
 0.008677376418730265,
 0.013065780080500466,
 0.009169867863295985,
 0.0070377761885861345,
 0.0

---
## 기타 하이퍼파라미터 튜닝
많은 회사에서 만든 하이퍼파라미터 최적화 서비스들을 이용.  
19장에서 **구글 클라우드 AI플랫폼의 하이퍼파라미터 튜닝 서비스**를 알아본다고 함.  
그 밖에 **진화 알고리즘을** 적용한 하이퍼파라미터 튜닝도 있다고 함. 구글의 **AutoML** 서비스를 한 번 써보고 싶음.

---
## 은닉층의 개수
복잡한 문제의 경우 심층 신경망이 얕은 신경망보다 **파라미터 효율성** 이 훨씬 좋다고 함.  
또한 계층 구조로 인해 같은 도메인의 문제를 해결할 경우 전체 모델을 다시 초기화하는 것 보다는 이전에 사용했던 모델의 초반 부분을 그대로 가져와 초기화하는 **전이 학습**은 모델의 수렴 속도을 훨씬 빠르게 해주고 필요한 데이터셋도 줄여준다고 함.

---
## 은닉층 뉴런 개수
>일반적으로 각 층의 뉴런을 점점 줄여서 깔때기처럼 구성함. 저수준의 많은 특성이 고수준의 적은 특성으로 합쳐질 수 있기 때문.  
하지만 요즘은 그런 구성이 일반적이지 않다고 함. 대부분의 경우 **모든 은닉층에 같은 크기를 사용해도 동일하거나 더 나은 성능을 낸다고 함.**  

>이러면 튜닝할 하이퍼파라미터도 각 층마다 한 개씩이 아니라 전체를 통틀어 한 개가 됨. 그래도 대부분 **다른 은닉층보다 첫 번째 은닉층을 크게 하는 것**이 도움이 된다고 함.  

층의 개수와 마찬가지로 과대적합이 시작되기 전까지 점진적으로 뉴런 수를 늘릴 수 있음.  
>하지만 실전에서는 **필요한 것보다 더 많은 층과 뉴런을 가진 모델을 선택하고, 그런 다음 과대적합을 막도록 조기종료나 규제 기법을 사용**하는 것이 간단하고 효과적이라고 함. 이를 **스트레치 팬츠**  방식이라고 함. 즉 꼭 맞는 사이즈의 바지를 찾는데 시간을 쓰지 말고 큰 스트레치 팬츠를 사고 알맞게 줄이라는 것임.  

한 층의 뉴런 수가 너무 적으면 입력에 있는 유용한 정보를 모두 유지할 수 있는 표현 능력을 가지지 못해 어려워서 그런 듯

---
## 학습률, 배치 크기, 기타 하이퍼파라미터
- **학습률**
> **가장 중요한 파라미터**.  일반적으로 최적의 학습률은 최대 학습률의 절반이라고 함(?? 처음 알음)  
좋은 학습률을 찾는 한 가지 방법은 간단하게 매우 낮은 학습률부터 점진적으로 큰 학습률로 바꿔가며 학습해보고 가장 좋은 것을 선택하는 것  
특히 배치 크기에 영향을 많이 받음. 다른 하이퍼파라미터가 바뀌면 학습률도 반드시 바뀌어야 함.
  
- **옵티마이저**
> 고전적인 평범한 미니배치 경사 하강법보다 더 좋은 옵티마이저를 선택하는 것도 매우 중요. 11장에서 알아본다고 함.

- **배치 크기**
> GPU 램에 맞는 가장 큰 배치 크기를 사용하는 것이 좋다고 함.  
한 가지 주의할 점으로 실전에서 큰 배치를 사용하면 특히 훈련 초기에 종종 불안정하게 학습된다고 함. 한 논문에 의하면 학습률 예열(작은 학습률로 훈련을 시작해서 점점 크게 하는 것)을 사용해 큰 배치 크기를 시도해 보는 것이 좋다고 함.

- **활성 함수**
> 일반적으로 **ReLU** 가 좋은 기본값임. 출력층의 활성 함수는 작업에 따라 달라짐.

- **반복 횟수**
> 대부분의 경우 훈련 반복 횟수는 튜닝할 필요가 없음. 대신 조기 종료를 사용.